Libraries and Functions

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from numpy import random
import scipy.stats
from scipy import odr
import pandas as pd
import statsmodels.formula.api as smf

def ols_regression(x, y, prob):
    """
    Return the linear regression parameters and their <prob> confidence intervals.
    ex:
    >>> linear_regression([.1,.2,.3],[10,11,11.5],0.95)
    """
    x = np.array(x)
    y = np.array(y)
    n = len(x)
    xy = x * y
    xx = x * x

    # estimates

    b1 = (xy.mean() - x.mean() * y.mean()) / (xx.mean() - x.mean()**2)
    b0 = y.mean() - b1 * x.mean()
    s2 = 1./n * sum([(y[i] - b0 - b1 * x[i])**2 for i in range(n)])
    #print('b0 = ',b0)
    #print('b1 = ',b1)
    #print('s2 = ',s2)
    
    #confidence intervals
    
    alpha = 1 - prob
    c1 = scipy.stats.chi2.ppf(alpha/2.,n-2)
    c2 = scipy.stats.chi2.ppf(1-alpha/2.,n-2)
    #print('the confidence interval of s2 is: ',[n*s2/c2,n*s2/c1])
    
    c = -1 * scipy.stats.t.ppf(alpha/2.,n-2)
    bb1 = c * (s2 / ((n-2) * (xx.mean() - (x.mean())**2)))**.5
    #print('the confidence interval of b1 is: ',[b1-bb1,b1+bb1])
    
    bb0 = c * ((s2 / (n-2)) * (1 + (x.mean())**2 / (xx.mean() - (x.mean())**2)))**.5
    #print('the confidence interval of b0 is: ',[b0-bb0,b0+bb0])
    return [b0, bb0, b1, bb1]

def odr_regression(x, y, delta = 1):
    df = pd.DataFrame({"x": x,"y": y})
    cov = df.cov()
    mean_x = df['x'].mean()
    mean_y = df['y'].mean()
    s_xx = cov['x']['x']
    s_yy = cov['y']['y']
    s_xy = cov['x']['y']

    slope = (s_yy  - delta * s_xx + np.sqrt((s_yy - delta * s_xx) ** 2 + 4 * delta * s_xy ** 2)) / (2 * s_xy)
    intercept = mean_y - slope  * mean_x

    return [slope, intercept]

Slope Study

In [ ]:
parts = ["val", "est"]
signum = [-1, +1]
val_deviation = [-7, -6.5, -6, -5.5, -5, -4.5, -4, -3.5, -3, -2.5, -2, -1.5, -1, -0.5, 0, 0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5, 5.5, 6, 6.5, 7]

number_points = 100
x = np.linspace(0, 1, number_points)
conf = 0.05
t_value = 1.984
sigma = 0.1

signums = list()
deviations = list()
ols_slopes = list()
ols_intercepts = list()
std_errors = list()
val_intercepts = list()
val_slopes = list()
conf_slopes = list()
conf_intercepts = list()

for sign in signum:
    
    for dev in val_deviation:
        
        slope = sign*random.uniform(0.35,0.66)
        y_intercept = 0.5-(slope*0.5)   #y-axis intercept
        slope_result = -1
        intercept_result = -1

        while abs(slope_result-slope)>0.001 or abs(y_intercept-intercept_result)>0.001:
            
            ##generate y-coordinates
            y = slope*x+y_intercept

            #gaussian band-width
            #sigma = random.uniform(0.05,0.21)
            band = random.normal(0,sigma,100)
            y = y + band

            ##OLS regression
            df = pd.DataFrame()
            df['x']=x
            df['y']=y
            ols = smf.ols('y ~ x', df).fit()
            predictions = ols.get_prediction(df).summary_frame(conf)

            slope_result = ols.params["x"]
            intercept_result = ols.params["Intercept"]

        val_slope = ols.params["x"] + ols.bse["x"]*dev
        val_intercept = 0.5-0.5*val_slope
        val = val_slope*x + val_intercept

        for part in parts:

            if part == "val":

                ##storing statistics
                signums.append(sign)
                deviations.append(dev)
                ols_slopes.append(ols.params["x"])
                ols_intercepts.append(ols.params["Intercept"])
                std_errors.append(ols.bse["x"])
                val_intercepts.append(val_intercept)
                val_slopes.append(val_slope)
                conf_slopes.append(ols.bse["x"]*t_value)
                conf_intercepts.append(ols.bse["Intercept"]*t_value)

                ##save data
                raw_data = pd.DataFrame(data = {"x": x, "y": y})
                #raw_data.to_csv("Slope_Study_Data/" + str(sign) + "_" + str(dev) + ".csv")

            ##plotting
            plt.figure(figsize=(8, 8))
            plt.scatter(x, y, s = 20, linewidths=0, color = "black")   #scatterplot
            if part == "val":
                plt.plot(x, val, color = "red") #validation
            plt.xlim([0,1])
            plt.ylim([0,1])
            plt.xticks([])
            plt.yticks([])

            #plt.savefig("Slope_Study_Vis/" + str(part) + "_" + str(sign) + "_" + str(dev) + ".png", format = "png", dpi = 300, bbox_inches='tight')

data_stats = pd.DataFrame(data = {'signum': signums, "deviation": deviations, "ols_slope": ols_slopes, "ols_intercepts": ols_intercepts, "std_error": std_errors, "val_intercept": val_intercepts, "val_slope": val_slopes, "conf_slope": conf_slopes, "conf_intercept": conf_intercepts})
#data_stats.to_csv("slope_study_data_stats.csv")


Visual Features Study

In [ ]:
features = ["error", "box", "conf"]
signum = [-1, +1]
val_deviation = [-7, -6.5, -6, -5.5, -5, -4.5, -4, -3.5, -3, -2.5, -2, -1.5, -1, -0.5, 0, 0.5, 1, 1.5, 2, 2.5, 3, 3.5, 4, 4.5, 5, 5.5, 6, 6.5, 7]

conf = 0.05

for sign in signum:
    for dev in val_deviation:

        data = pd.read_csv("Study_Data/" + str(sign) + "_" + str(dev) + ".csv")
        x = data["x"]
        y = data["y"]
        
        ##OLS regression
        df = pd.DataFrame()
        df['x']=x
        df['y']=y
        ols = smf.ols('y ~ x', df).fit()
        predictions = ols.get_prediction(df).summary_frame(conf)

        val_slope = ols.params["x"] + ols.bse["x"]*dev
        val_intercept = 0.5-0.5*val_slope
        val = val_slope*x + val_intercept

        for feature in features:

            fig, ax = plt.subplots(figsize=(8, 8))
            ax.scatter(x, y, s = 20, linewidths=0, color = "black") 
            ax.plot(x, val, '-', color = "red")
            ax.set_xlim([0,1])
            ax.set_ylim([0,1])
            ax.set_xticks([])
            ax.set_yticks([])

            if feature == "error":
                list_max = np.where(np.array(y) > np.array(val), y, val)
                list_min = np.where(np.array(y) < np.array(val), y, val)
                ax.vlines(x, list_min, list_max, colors="blue", linestyles="solid", linewidths=0.6, alpha = 0.5)

            if feature == "box":
                box_max = np.round(val, 4) + 1
                box_min = np.round(val, 4) - 1
                while len([i for i, j in zip(np.round(y,4), np.round(box_max, 4)) if i == j]) != 1 and max(box_max)>0:
                    box_max = box_max - 0.0001
                while len([i for i, j in zip(np.round(y,4), np.round(box_min, 4)) if i == j]) != 1 and min(box_min)<1:
                    box_min = box_min + 0.0001
                ax.fill_between(x, val_slope*x + box_min[0], val_slope*x + box_max[0], alpha = 0.1, color = "blue")

            if feature == "conf":
                diff_lower = predictions['mean']-predictions['mean_ci_lower']
                diff_upper = predictions['mean_ci_upper']-predictions['mean']
                val_ci_lower = val-diff_lower
                val_ci_upper = val+diff_upper
                ax.fill_between(x, val_ci_lower, val_ci_upper, alpha=0.1, color = "blue")   #fake validation conf_interval
                
            #plt.savefig("Features_Study_Vis/" + str(feature) + "_" + str(sign) + "_" + str(dev) + ".png", format = "png", dpi = 300, bbox_inches='tight')